In [2]:
!pip install bertviz transformers
!pip install jsonlines
!pip install -U openai-whisper
!apt-get install ffmpeg
!pip install botocore
!pip install boto3
!pip install jiwer

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 157.6/157.6 kB 1.8 MB/s eta 0:00:00a 0:00:01m
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.0/11.0 MB 51.9 MB/s eta 0:00:0000:010:01
  Attempting uninstall: botocore
    Found existing installation: botocore 1.34.69
    Uninstalling botocore-1.34.69:
      Successfully uninstalled botocore-1.34.69
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
aiobotocore 2.12.3 requires botocore<1.34.70,>=1.34.41, but you have botocore 1.29.165 which is incompatible.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.6/798.6 kB 4.2 MB/s eta 0:00:0000:0100:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 168.1/168.1 MB 2.3 MB/s eta 0:00:0000:0100:02
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 

In [4]:
import os
os.environ["CUDA_VISIBLE_DEVICES"]="1"

from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show
from bertviz import head_view
from transformers import AutoModel
from torch import nn
from transformers import AutoConfig
import torch
from math import sqrt
import torch.nn.functional as F
import librosa

import jsonlines
from torch.utils.data import DataLoader, Dataset

In [5]:
import torch

device = 'cuda'
sampling_rate = 16000
print(torch.cuda.is_available(),
torch.cuda.device_count())

True 1


# Transformer

![Image Title](/kaggle/input/images/transformer.png)
*Encoder-decoder architecture of the Transformer, with the encoder shown in the upper half of the figure and the decoder in the lower half.*

## Transformer Encoder

The Transformer’s encoder consists of many encoder layers stacked next to each other. Each encoder layer receives a sequence of embeddings and feeds them through the following sub-layers:
1. A multi-head self-attention layer.
2. A shared feed-forward layer.

The output embeddings of each encoder layer have the same size as the inputs.

The main role of the encoder stack is to "update" the input embeddings to produce representations that encode some contextual information in the sequence. For example the word "apple" will be updated to be more "company-like" and less "fruit-like" if the words "keynote" or "phone" are close to the word.

Each of these sub-layers also has a skip connection and layer normalization, which are standard tricks to train deep neural networks effectively.

![Image Title](/kaggle/input/images/encoder.png)

*Zooming into the encoder layer.*

## Self-Attention

**Attention** is a mechanism that allows neural networks to assign a different amount of weight or "attention" to each element in a sequence. For text sequences, the elements are token embeddings. Each token is mapped to a vector of some fixed dimension. For example, in BERT each token is represented as a 768-dimensional vector.

The main idea behind self-attention is that instead of using a fixed embedding for each token, we can use the whole sequence to compute a weighted average of each embedding. Another way to formulate this is to say that given a sequence of token embeddings $x_1, \ldots, x_n$, self-attention produces a sequence of new embeddings $x'_1, \ldots, x'_n$ where each $x'_i$ is a linear combination of all the $x_j$:

$$x'_i = \sum_{j=1}^{n} w_{ij}x_j$$

The coefficients $(w_{ji})$ are called attention weights and are normalized so that $\sum_{j} w_{ji} = 1$.

Embeddings that are generated in this way are called contextualized embeddings.

### Time flies like an arrow; fruit flies like a banana

![Image Title](images/contextualized_embeddings.png)

*Diagram showing how self-attention updates raw token embeddings (upper) into contextualized embeddings (lower) to create representations that incorporate information from the whole sequence.*

### Scaled Dot-Product Attention

There are several ways to implement a self-attention layer, but the most common is scaled dot-product attention from the Attention is All You Need paper where the Transformer was introduced. There are four main steps needed to implement this mechanism:
1. **Create query, key, and value vectors.** Each token embedding is projected into query, key, and value vectors.
2. **Compute attention scores.** Determine how much the query and key vectors relate using a similarity function. As the name suggests, the similarity function for scaled dot-product attention is the dot-product, computed efficiently using matrix multiplication of the embeddings. Similar queries and keys will have a large dot product, while those that don't share much in common will have little to no overlap. The outputs from this step are called the attention scores, and for a sequence with $n$ input tokens, there is a corresponding $n \times n$ matrix of attention scores.
3. **Compute attention weights.** Dot products can, in general, produce arbitrarily large numbers, which can destabilize the training process. To handle this, the attention scores are first multiplied by a scaling factor to normalize their variance and then normalized with a softmax to ensure all the column values sum to one. The resulting $n \times n$ matrix now contains all the attention weights $w_{ji}$.
4. **Update the token embeddings.** Once the attention weights are computed, we multiply them by the value vector $( v_1, \ldots, v_n )$ to obtain an updated representation for embedding $(x'_i = \sum_{j} w_{ji}v_j )$.

**The first step of self-attention calculation**: For each word, we create a Query vector, a Key vector, and a Value vector. These vectors are created by multiplying the embedding by three matrices that we trained during the training process.

Notice that these new vectors are smaller in dimension than the embedding vector. Their dimensionality is 64, while the embedding and encoder input/output vectors have dimensionality of 512. They DON'T HAVE to be smaller, this is an architecture choice to make the computation of multiheaded attention (mostly) constant.

![Image Title](images/qkv.png)

*Multiplying $x_1$ by the $W_Q$ weight matrix produces $q_1$, the "query" vector associated with that word. We end up creating a "query", a "key", and a "value" projection of each word in the input sentence.*

![Image Title](images/self_attention_process.png)

*Self-attention calculation.*

**The second step of self-attention calculation**: We're calculating the self-attention for the first word in this example, "Thinking". We need to score each word of the input sentence against this word. The score determines how much focus to place on other parts of the input sentence as we encode a word at a particular position.

The score is calculated by taking the dot product of the query vector with the key vector of the respective word we're scoring. So, if we're processing the self-attention for the word in position #1, the first score would be the dot product of $q_1$ and $k_1$. The second score would be the dot product of $q_1$ and $k_2$.

**The third and fourth steps** are to divide the scores by 8 (the square root of the dimension of the key vectors used in the paper—64), which leads to more stable gradients. Other possible values here could be used, but this is the default. Then, the result is passed through a softmax operation. Softmax normalizes the scores to be positive and add up to 1.

This softmax score determines how much each word will be expressed at this position. Clearly, the word at this position will have the highest softmax score, but sometimes, attending to another word relevant to the current word is helpful.

**The fifth step** is to multiply each value vector by the softmax score (in preparation for summarizing them). The intuition here is to keep intact the values of the word(s) we want to focus on and drown out irrelevant words (by multiplying them by tiny numbers like 0.001, for example).

**The sixth step** is to sum up the weighted value vectors. This produces the output of the self-attention layer at this position (for the first word).

$$\text{Attention}(Q, K, V) = \text{softmax}(\frac{QK^T}{\sqrt{d_k}})V$$

![Image Title](images/attention_matrix_form.png)

*The self-attention calculation in matrix form.*

That concludes the self-attention calculation. The resulting vector is one we can send along to the feed-forward neural network.

In [5]:
model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = BertModel.from_pretrained(model_ckpt)
config = AutoConfig.from_pretrained(model_ckpt)

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

100%|██████████| 440473133/440473133 [00:11<00:00, 38867452.49B/s]


In [6]:
text = "time flies like an arrow"
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [4]:
text = "fruit flies like a banana"
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Attention implementation

In [7]:
text = "time flies like an arrow"

inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)
inputs.input_ids

tensor([[ 2051, 10029,  2066,  2019,  8612]])

In [8]:
tokens = tokenizer.convert_ids_to_tokens(inputs.input_ids[0])
tokens

['time', 'flies', 'like', 'an', 'arrow']

Then, we need to create some dense embeddings. "Dense" in this context means that each entry in the embeddings contains a non-zero value.

In [9]:
config

BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "position_embedding_type": "absolute",
  "transformers_version": "4.39.3",
  "type_vocab_size": 2,
  "use_cache": true,
  "vocab_size": 30522
}

Each input ID will be mapped to one of the 30,522 embedding vectors stored in `nn.Embedding`, each with a size of 768. Note that the token embeddings at this point are independent of their context.

In [8]:
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

In [9]:
# look-up table
inputs_embeds = token_emb(inputs.input_ids)
inputs_embeds.size()

torch.Size([1, 5, 768])

### Embedding Layer vs Linear Layer

Both `nn.Embedding` and a linear layer (`nn.Linear`) in `PyTorch` are used to transform input data into a different representation, but they serve different purposes and have different characteristics:

1. Purpose:
    * **Embedding Layer** (`nn.Embedding`): Specifically designed for handling sparse data where the input is categorical, such as word embeddings in NLP tasks. It maps discrete indices (representing words or tokens) to dense vectors, capturing semantic relationships between tokens.
    * **Linear Layer** (`nn.Linear`): A general-purpose layer used for linear transformations of input data. It's typically used for tasks such as classification, regression, or other tasks with continuous input features.

2. Input Data:
    * **Embedding Layer**: Expects integer indices as input, representing categories or tokens. Each integer index corresponds to a row in the embedding matrix.
    * **Linear Layer**: Expects continuous-valued input data, such as feature vectors or the output of other layers.

3. Output:
    * **Embedding Layer**: Produces dense vector representations (embeddings) of the input tokens. The vocabulary size and the embedding dimension specified during initialization determine the output dimensions.
    * **Linear Layer**: Produces a linear transformation of the input data. The output dimensions are determined by the number of output units specified during initialization.

4. Parameters:
    * **Embedding Layer**: The parameters are the embedding matrix itself, which is learned during training. The vocabulary size and embedding dimension determine the size of the embedding matrix.
    * **Linear Layer**: The parameters are the weight matrix and bias vector, both learned during training. The size of the weight matrix is determined by the input and output dimensions specified during initialization.

5. Usage:
    * **Embedding Layer**: Primarily used in NLP tasks to represent words or tokens as dense vectors. It is often used as the first layer in neural network architectures for processing text.
    * **Linear Layer**: Widely used in various neural network architectures for transforming input data or connecting layers. It's used in tasks like classification, regression, or any other task requiring linear transformations.

The next step is to create the query, key, and value vectors and calculate the attention scores using the dot-product as the similarity function:

In [10]:
# We’ll see later that the query, key, and value vectors are generated by applying independent weight matrices W_Q, W_K, W_V to the embeddings, but for now we’ve kept them equal for simplicity.

# In scaled dot-product attention, the dot-products are scaled by the size of the embedding vectors so that we don’t get too many large numbers during training that can cause the softmax we will apply next to saturate.

query = key = value = inputs_embeds
dim_k = key.size(-1)
scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k) # bmm performs a batch matrix-matrix product
scores.size()

torch.Size([1, 5, 5])

In [11]:
weights = F.softmax(scores, dim=-1)
print(weights.shape)

torch.Size([1, 5, 5])


In [12]:
scores

tensor([[[25.8431, -2.1171, -1.0447,  0.4381,  2.0931],
         [-2.1171, 25.3569, -0.4879, -0.6890, -0.5012],
         [-1.0447, -0.4879, 27.0742, -1.2382,  0.0499],
         [ 0.4381, -0.6890, -1.2382, 27.0541, -0.9226],
         [ 2.0931, -0.5012,  0.0499, -0.9226, 29.2967]]],
       grad_fn=<DivBackward0>)

In [13]:
weights

tensor([[[1.0000e+00, 7.1950e-13, 2.1027e-12, 9.2625e-12, 4.8472e-11],
         [1.1700e-12, 1.0000e+00, 5.9666e-12, 4.8798e-12, 5.8879e-12],
         [6.1391e-13, 1.0713e-12, 1.0000e+00, 5.0590e-13, 1.8344e-12],
         [2.7595e-12, 8.9400e-13, 5.1620e-13, 1.0000e+00, 7.0777e-13],
         [1.5333e-12, 1.1453e-13, 1.9874e-13, 7.5151e-14, 1.0000e+00]]],
       grad_fn=<SoftmaxBackward0>)

In [14]:
torch.bmm(weights, value).shape

torch.Size([1, 5, 768])

In [15]:
weights = F.softmax(scores, dim=-1)
weights

tensor([[[1.0000e+00, 7.1950e-13, 2.1027e-12, 9.2625e-12, 4.8472e-11],
         [1.1700e-12, 1.0000e+00, 5.9666e-12, 4.8798e-12, 5.8879e-12],
         [6.1391e-13, 1.0713e-12, 1.0000e+00, 5.0590e-13, 1.8344e-12],
         [2.7595e-12, 8.9400e-13, 5.1620e-13, 1.0000e+00, 7.0777e-13],
         [1.5333e-12, 1.1453e-13, 1.9874e-13, 7.5151e-14, 1.0000e+00]]],
       grad_fn=<SoftmaxBackward0>)

In [16]:
weights.sum(dim=-1)

tensor([[1., 1., 1., 1., 1.]], grad_fn=<SumBackward1>)

In [17]:
attn_outputs = torch.bmm(weights, value)
attn_outputs.shape

torch.Size([1, 5, 768])

In [18]:
attn_outputs

tensor([[[ 2.1856e+00,  2.3719e-01,  5.9591e-01,  ...,  1.6541e+00,
          -2.2697e-01, -1.5417e-01],
         [-1.3669e+00, -4.5329e-01, -6.8402e-01,  ..., -4.8425e-02,
           6.9000e-01, -3.4179e-01],
         [ 1.3553e-01, -1.1197e+00, -1.4007e+00,  ...,  1.1851e-01,
          -1.5931e+00, -1.1045e+00],
         [-6.9330e-01,  3.7640e-01,  1.5337e+00,  ..., -5.6836e-01,
          -1.0827e+00, -9.6147e-01],
         [ 2.0786e-03, -8.7819e-01,  3.1212e-01,  ...,  1.6152e+00,
          -9.8263e-01, -3.2690e-02]]], grad_fn=<BmmBackward0>)

In [19]:
def scaled_dot_product_attention(query, key, value):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    weights = F.softmax(scores, dim=-1)
    return torch.bmm(weights, value)

In practice, the self-attention layer applies three independent linear transformations to each embedding to generate the query, key, and value vectors.

These transformations project the embeddings and each projection carries its own set of learnable parameters, which allows the self-attention layer to focus on different semantic aspects of the sequence.

In [20]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)

    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(self.q(hidden_state), self.k(hidden_state), self.v(hidden_state))
        return attn_outputs

### Multi-Headed Attention

It also turns out to be beneficial to have multiple sets of linear projections, each one representing a so-called attention head.

But why do we need more than one attention head? The reason is that softmax of one head tends to focus on mostly one aspect of similarity.

Having several heads allows to focus on several aspects at once. For instance one head can focus on subject-verb interaction, whereas another finds nearby adjectives.

Obviously, we don’t handcraft these relations into the model and they are fully learned from the data.

![Image Title](images/multi_head_att.png)

*Multi-headed attention*

In [21]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList([AttentionHead(embed_dim, head_dim) for _ in range(num_heads)] )
        self.output_linear = nn.Linear(embed_dim, embed_dim)
        
    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

In practice `head_dim` is chosen to be a multiple of `embed_dim` so that the computation across each head is constant. For example in BERT has 12 attention heads, so the dimension of each head is 768/12 = 64.

In [22]:
multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)
attn_output.size()

torch.Size([1, 5, 768])

In [23]:
attn_output

tensor([[[-0.1212, -0.0313,  0.1591,  ...,  0.0748,  0.0909,  0.1840],
         [-0.1439, -0.1211,  0.1224,  ...,  0.0935,  0.0102,  0.1706],
         [-0.1026, -0.1296,  0.1588,  ...,  0.0783,  0.0108,  0.1866],
         [-0.0641, -0.1473,  0.0774,  ...,  0.0525,  0.0317,  0.1762],
         [-0.1801, -0.1613,  0.1175,  ...,  0.0094, -0.0077,  0.2061]]],
       grad_fn=<ViewBackward0>)

In [24]:
model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)
sentence_a = "time flies like an arrow"
sentence_b = "fruit flies like a banana"
viz_inputs = tokenizer(sentence_a, sentence_b, return_tensors='pt')
attention = model(**viz_inputs).attentions
sentence_b_start = (viz_inputs.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])
head_view(attention, tokens, sentence_b_start, heads=[8])

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

<IPython.core.display.Javascript object>

### Feed Forward Layer

The feed forward sub-layer in the encoder and decoder is just a simple 2-layer fully-connected neural network, but with a twist: instead of processing the whole sequence of embeddings as a single vector, it processes each embedding independently.

In [25]:
class FeedForward(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu = nn.GELU()
        self.dropout = nn.Dropout(config.hidden_dropout_prob)

    def forward(self, x):
        print(x.shape)
        x = self.linear_1(x)
        print(x.shape)
        x = self.gelu(x)
        x = self.linear_2(x)
        x = self.dropout(x)
        return x

In [26]:
feed_forward = FeedForward(config)
ff_outputs = feed_forward(attn_outputs)
ff_outputs.size()

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])


torch.Size([1, 5, 768])

### Adding Layer Normalization

![Image Title](images/normalization.png)

*Different arrangements of layer normalization in a transformer encoder layer.*

In [27]:
class TransformerEncoderLayer(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
        self.layer_norm_2 = nn.LayerNorm(config.hidden_size)
        self.attention = MultiHeadAttention(config)
        self.feed_forward = FeedForward(config)
        
    def forward(self, x):
        # Apply layer normalization and then copy input into query, key, value
        hidden_state = self.layer_norm_1(x)
        # Apply attention with a skip connection
        x = x + self.attention(hidden_state)
        # Apply feed-forward layer with a skip connection
        x = x + self.feed_forward(self.layer_norm_2(x))
        return x

In [28]:
encoder_layer = TransformerEncoderLayer(config)
inputs_embeds.shape, encoder_layer(inputs_embeds).size()

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])


(torch.Size([1, 5, 768]), torch.Size([1, 5, 768]))

## Positional Encodings

In [29]:
class Embeddings(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.token_embeddings = nn.Embedding(config.vocab_size,
                                             config.hidden_size)
        self.position_embeddings = nn.Embedding(config.max_position_embeddings,
                                                config.hidden_size)
        self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
        self.dropout = nn.Dropout()
        
    def forward(self, input_ids):
        # Create position IDs for input sequence
        seq_length = input_ids.size(1)
        position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0) # create token and position embeddings
        token_embeddings = self.token_embeddings(input_ids)
        position_embeddings = self.position_embeddings(position_ids)
        print(position_embeddings)
        # Combine token and position embeddings
        embeddings = token_embeddings + position_embeddings
        embeddings = self.layer_norm(embeddings)
        embeddings = self.dropout(embeddings)
        return embeddings

In [30]:
embedding_layer = Embeddings(config)
embedding_layer(inputs.input_ids).size()

tensor([[[ 0.9510, -1.6721,  0.1688,  ..., -0.2077,  1.0721,  0.6463],

         [-0.4921, -0.0740,  1.4788,  ..., -0.7184, -1.0116,  0.4600],

         [-0.8165,  1.2812, -0.4372,  ..., -0.6765,  1.1058, -0.0846],

         [ 0.3262, -0.3868, -0.2307,  ..., -0.0365,  1.0664, -0.2932],

         [-0.1875, -0.7765,  0.3548,  ...,  2.9257,  1.1251,  0.0363]]],

       grad_fn=<EmbeddingBackward0>)


torch.Size([1, 5, 768])

In [31]:
config.max_position_embeddings

512

In [32]:
class TransformerEncoder(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.embeddings = Embeddings(config)
        self.layers = nn.ModuleList([TransformerEncoderLayer(config) for _ in range(config.num_hidden_layers)])
    def forward(self, x):
        x = self.embeddings(x)
        for layer in self.layers:
            x = layer(x)
        return x

In [33]:
encoder = TransformerEncoder(config)
encoder(inputs.input_ids).size()

tensor([[[-0.9269, -0.2352, -0.6885,  ...,  0.1051, -0.2508,  0.5033],

         [-0.4158, -1.0667, -0.3377,  ...,  1.6644, -0.6727,  0.4324],

         [ 0.2909, -0.4881,  0.8657,  ...,  0.4432, -0.1674,  0.0734],

         [ 0.4359,  0.2352, -1.3667,  ...,  2.3093, -0.8356, -0.8579],

         [ 1.0572,  0.3104,  0.5621,  ...,  1.9411,  0.4417,  0.5687]]],

       grad_fn=<EmbeddingBackward0>)

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1,

torch.Size([1, 5, 768])

In [34]:
# For classification tasks, it is common practice to just use the hidden state associated with the [CLS] token as the input feature.

class TransformerForSequenceClassification(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.encoder = TransformerEncoder(config)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)

    def forward(self, x):
        x = self.encoder(x)[:, 0, :] # select hidden state of [CLS] token
        x = self.dropout(x)
        x = self.classifier(x)
        return x

In [35]:
config.num_labels = 3
encoder_classifier = TransformerForSequenceClassification(config)
encoder_classifier(inputs.input_ids).size()

tensor([[[-0.1515, -0.1657,  0.0414,  ..., -0.5167, -0.7033,  1.1934],

         [ 0.9560, -0.1290,  1.1958,  ...,  1.3158,  0.2679,  0.1183],

         [-0.3716,  0.5560, -0.0558,  ..., -0.1341, -0.8486,  0.9830],

         [ 0.6791, -1.3523,  0.0791,  ...,  0.1129,  0.0725, -2.1017],

         [-0.5500,  1.9636, -0.5887,  ..., -0.6279,  0.5956, -0.3951]]],

       grad_fn=<EmbeddingBackward0>)

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1, 5, 3072])

torch.Size([1, 5, 768])

torch.Size([1,

torch.Size([1, 3])

## Transformer Decoder

![Image Title](images/decoder.png)

*Zooming into the Transformer decoder layer*

## Whisper summary

![Image Title](images/whisper_tasks.png)

*Whisper tasks.*

![Image Title](images/training_data.png)

*Training data. Of those 680k hours of audio, 117k hours cover 96 other languages.*

### Approach

**Data-processing**

1. No specific data pre-processing applied.
2. Developed several automated filtering methods to improve transcript quality.
3. Developed many heuristics to detect and remove machine-generated transcripts from the training dataset.
    1. An all-uppercase or all-lowercase transcript is very unlikely to be human-generated.
4. Use an audio language detector to ensure that the spoken language matches the language of the transcript according to CLD2.
5. Break audio files into 30-second segments paired with the subset of the transcript that occurs within that time segment.
6. Train on all audio, including segments with no speech (though with sub-sampled probability), and use these segments as training data for voice activity detection.
7. After training an initial model, they aggregated information about its error rate on training data sources. They manually inspected these data sources, sorting by a combination of high error rates and data source size to identify and remove low-quality ones efficiently.

**Model**

1. Using an off-the-shelf architecture avoids confounding our findings with model improvements.
2. Choose an encoder-decoder Transformer.
3. All audio is re-sampled to 16,000 Hz, and an 80-channel log-magnitude Mel spectrogram representation is computed on 25 millisecond windows with a stride of 10 milliseconds.
4. They globally scale the input between -1 and 1 with approximately zero mean across the pre-training dataset for feature normalization.
5. They use the same byte-level BPE text tokenizer used in GPT-2 for the English-only models and refit the vocabulary (but keep the same size) for the multilingual models to avoid excessive fragmentation on other languages since the GPT-2 BPE vocabulary is English-only.

![Image Title](images/whisper_architecture.png)

*Whisper architecture.*

**Multitask Format**

1. Since their decoder is an audio-conditional language model, they also train it to condition the history of the transcript's text in the hope that it will learn to use longer-range text context to resolve ambiguous audio.
2. Specifically, with some probability, they add the transcript text preceding the current audio segment to the decoder's context.
3. A sequence-to-sequence Transformer model is trained on many different speech processing tasks, including multilingual speech recognition, speech translation, spoken language identification, and voice activity detection. These tasks are jointly represented as a sequence of tokens to be predicted by the decoder, allowing for a single model to replace many stages of a traditional speech-processing pipeline.

![Image Title](images/whisper_multitask.png)

# Homework

Implement class `Trainer` to fine-tune Whisper (tiny) on Toronto dataset. You may refer to the HF Trainer, but you have to implement it on your own.

Divide dataset into train, eval and test. Compare performance on test set using original model, original model with original LM, fine-tuned model, fine-tuned model with new LM.

**Sources**:
- Link to the Toronto dataset: https://drive.google.com/file/d/1j9d91QqE7_WnOnmEmidtOG55tpmxQUeJ/view?usp=sharing.
- Another training dataset: https://huggingface.co/datasets/skypro1111/whisper-dataset-ytb-uk. *I'm not sure about its quality*.

# Dataset preparation

In [6]:
with jsonlines.open("/kaggle/input/toronto-dataset/labels.jsonl", 'r') as reader:
    dataset = {path: label for line in reader for path, label in line.items() if os.path.exists("/kaggle/input/toronto-dataset/"+"/".join(path.split("/")[1:])) and label != ""}

len(dataset)

18210

In [54]:
import random

random_sample = random.sample(dataset.items(), k=1000)
random_sample_dict = dict(random_sample)

len(random_sample_dict)

/tmp/ipykernel_34/2373433570.py:3: DeprecationWarning: Sampling from a set deprecated
since Python 3.9 and will be removed in a subsequent version.
  random_sample = random.sample(dataset.items(), k=1000)


1000

In [55]:
from sklearn.model_selection import train_test_split

paths = list(random_sample_dict.keys())
labels = list(random_sample_dict.values())

train_paths, temp_paths, train_labels, temp_labels = train_test_split(paths, labels, test_size=0.2, random_state=42)

validation_paths, test_paths, validation_labels, test_labels = train_test_split(temp_paths, temp_labels, test_size=0.5, random_state=42)

train_set = {path: label for path, label in zip(train_paths, train_labels)}
validation_set = {path: label for path, label in zip(validation_paths, validation_labels)}
test_set = {path: label for path, label in zip(test_paths, test_labels)}

print("Number of samples in train set:", len(train_set))
print("Number of samples in validation set:", len(validation_set))
print("Number of samples in test set:", len(test_set))

Number of samples in train set: 800
Number of samples in validation set: 100
Number of samples in test set: 100


## Whisper (without fine-tuning)

In [12]:
import whisper

model = whisper.load_model("tiny").to(device)

100%|██████████████████████████████████████| 72.1M/72.1M [00:00<00:00, 149MiB/s]


In [8]:
audio_path, text = list(train_set.items())[0]
audio_path = "/kaggle/input/toronto-dataset/"+"/".join(audio_path.split("/")[1:])
result = model.transcribe(audio_path)
print(result["text"])
print(text)

 Та, через епідає мію зупинився рух моторних човній, і канали стали часті, що ми ніч буть коли.
Там через епідемію зупинився рух моторних човнів, і канали стали чистішими, ніж будь-коли.


In [13]:
import torch
from torch.utils.data import Dataset

class CustomDataset(Dataset):
    def __init__(self, data):
        self.data = data

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        audio_path, transcription = self.data[idx]
        modified_path = "/kaggle/input/toronto-dataset/" + "/".join(audio_path.split("/")[1:])
        return modified_path, transcription


In [37]:
kwargs = {"num_workers": 1, "pin_memory": True}

test_loader = DataLoader(dataset=CustomDataset(list(test_set.items())),
                            batch_size=1,
                            shuffle=False,
                            **kwargs)

len(test_loader)

10

In [3]:
from datasets import load_metric

wer = load_metric('wer')
cer = load_metric('cer')

/opt/conda/lib/python3.10/site-packages/datasets/load.py:756: FutureWarning: The repository for wer contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.18.0/metrics/wer/wer.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric from the next major release of `datasets`.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/datasets/load.py:756: FutureWarning: The repository for cer contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.18.0/metrics/cer/cer.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric from the next major release of

In [38]:
predictions_all = []
transcriptions_all = []

for batch in test_loader:
    pathes, transcriptions = batch 
    result = model.transcribe(pathes[0])
    predictions = result["text"]

#     print('---')
#     print('Predictions:')
#     print(predictions)
#     print('References:')
#     print(transcriptions)
#     print('---')

    predictions_all.append(predictions)
    transcriptions_all.extend(transcriptions)

In [39]:
wer_value = round(wer.compute(predictions=predictions_all, references=transcriptions_all), 4)
cer_value = round(cer.compute(predictions=predictions_all, references=transcriptions_all), 4)

print(f'WER: {wer_value} | CER: {cer_value}')

WER: 0.6519 | CER: 0.2965


## Whisper tokenizer and featureExtractor

In [62]:
from transformers import WhisperFeatureExtractor
from transformers import WhisperTokenizer
from transformers import WhisperForConditionalGeneration
from transformers import WhisperProcessor

# feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-tiny", language="Ukrainian")
# tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-tiny", language="Ukrainian", task="transcribe")
processor = WhisperProcessor.from_pretrained("openai/whisper-tiny", language="Ukrainian", task="transcribe")
model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-tiny").to(device)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [35]:
audio_path, text = list(train_set.items())[0]
audio_path = "/kaggle/input/toronto-dataset/"+"/".join(audio_path.split("/")[1:])

input_str = text
labels = processor.tokenizer(input_str).input_ids
decoded_with_special = processor.tokenizer.decode(labels, skip_special_tokens=False)
decoded_str = processor.tokenizer.decode(labels, skip_special_tokens=True)

print("Labels: ", labels)
print(f"Input:                 {input_str}")
print(f"Decoded w/ special:    {decoded_with_special}")
print(f"Decoded w/out special: {decoded_str}")
print(f"Are equal:             {input_str == decoded_str}")

Labels:  [50258, 50280, 50359, 50363, 5594, 5594, 5594, 5594, 5594, 4589, 2933, 21239, 386, 12857, 1148, 13057, 14760, 8049, 11401, 5583, 3776, 14706, 740, 13306, 5608, 18686, 30239, 1827, 4756, 11, 22211, 1784, 8187, 435, 18752, 36397, 681, 43649, 1997, 755, 1885, 859, 9554, 1253, 1827, 41765, 18389, 13, 50257]
Input:                 ААААА!!! Ситуацію хоч якось намагаються виправити активісти, волонтери та деякі екосвідомі громади.
Decoded w/ special:    <|startoftranscript|><|uk|><|transcribe|><|notimestamps|>ААААА!!! Ситуацію хоч якось намагаються виправити активісти, волонтери та деякі екосвідомі громади.<|endoftext|>
Decoded w/out special: ААААА!!! Ситуацію хоч якось намагаються виправити активісти, волонтери та деякі екосвідомі громади.
Are equal:             True


In [38]:
waveform, sr = librosa.load(audio_path)
input_features = processor(waveform).input_features
print(input_features[0].shape)
print(input_features)

It is strongly recommended to pass the `sampling_rate` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


(80, 3000)
[array([[ 0.42777407,  0.52328694,  0.4094805 , ..., -0.5587741 ,
        -0.5587741 , -0.5587741 ],
       [ 0.36229134,  0.62041   ,  0.34660965, ..., -0.5587741 ,
        -0.5587741 , -0.5587741 ],
       [ 0.23975033,  0.62807477,  0.48226666, ..., -0.5587741 ,
        -0.5587741 , -0.5587741 ],
       ...,
       [-0.1867696 , -0.26815403, -0.2832346 , ..., -0.5587741 ,
        -0.5587741 , -0.5587741 ],
       [-0.29987955, -0.24087632, -0.3913852 , ..., -0.5587741 ,
        -0.5587741 , -0.5587741 ],
       [-0.40737307, -0.43052423, -0.49738884, ..., -0.5587741 ,
        -0.5587741 , -0.5587741 ]], dtype=float32)]


## WhisperCustom dataset

In [10]:
import re
from torch.utils.data import DataLoader, Dataset

class WhisperCustomDataset(Dataset):
    def __init__(self, dataset, processor, sr):
        self.paths = list(dataset.keys())
        self.labels = list(dataset.values())
        self.processor = processor
        self.sr = sr

    def __len__(self):
        return len(self.paths)

    def __getitem__(self, idx):
        path = self.paths[idx]
        target_transcription = self.labels[idx]
        target_transcription = self.normalize(target_transcription)
 
        audio_input, _ = librosa.load("/kaggle/input/toronto-dataset/"+"/".join(path.split("/")[1:]), sr=self.sr)
        features = self.processor([audio_input], sampling_rate=self.sr, return_tensors='pt').input_features
    
        labels = self.processor.tokenizer(target_transcription).input_ids
        return {"input_features": features, "labels": labels, "target_transcriptions": target_transcription}
    
    def normalize(self, text):
        text = text.lower()
        text = re.sub(r'\[[^\[\]]*\]', "", text)
        text = re.sub(r'\([^()]*\)', "", text)
        text = re.sub("\s+", " ", text)
        return text.strip()

## Collate func

In [109]:
dataset_hehe = WhisperCustomDataset(test_set, processor, sampling_rate)

dataset_elements = []
for el in dataset_hehe:
    dataset_elements.append(el)
    
len(dataset_hehe)

10

In [110]:
input_features = [{"input_features": feature["input_features"]} for feature in dataset_elements]
batch = processor.feature_extractor.pad(input_features, return_tensors="pt")

# get the tokenized label sequences
label_features = [{"input_ids": feature["labels"]} for feature in dataset_elements]
# pad the labels to max length
labels_batch = processor.tokenizer.pad(label_features, return_tensors="pt")

# replace padding with -100 to ignore loss correctly
labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

print(features_batch.input_features.shape, labels_batch.input_ids.shape)


torch.Size([10, 80, 3000]) torch.Size([10, 58])


In [12]:
def collate_fn(batch):
    input_features = [{"input_features": feature["input_features"]} for feature in batch]
    input_features_batch = processor.feature_extractor.pad(input_features, return_tensors="pt")
    label_features = [{"input_ids": feature["labels"]} for feature in batch]
    labels_batch = processor.tokenizer.pad(label_features, return_tensors="pt")
    # replace padding with -100 to ignore loss correctly
    #labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)
    return input_features_batch, labels_batch

## Whisper (using processor and model, without fine-tuning)

In [ ]:
from datasets import load_metric

wer = load_metric('wer')
cer = load_metric('cer')

In [13]:
kwargs = {"num_workers": 1, "pin_memory": True}

test_loader = DataLoader(dataset=WhisperCustomDataset(test_set, processor, sampling_rate),
                            batch_size=10,
                            shuffle=False,
                            collate_fn=collate_fn,
                            **kwargs)

len(test_loader)

1

In [51]:
predictions_all = []
transcriptions_all = []

for batch in test_loader:    
    features, labels = batch 
    attention_mask = labels["attention_mask"].to(device)
    labels = labels["input_ids"].to(device)
    input_values = features["input_features"].to(device)
    input_values = input_values.squeeze()
    
    with torch.no_grad():
        logits = model(input_values, decoder_input_ids=labels).logits
        
    predicted_ids = torch.argmax(logits, dim=-1)
    predicted_ids = predicted_ids.masked_fill(attention_mask.ne(1), processor.tokenizer.pad_token_id)
    predictions = processor.batch_decode(predicted_ids, skip_special_tokens=True)
    transcriptions = processor.batch_decode(labels, skip_special_tokens=True)

    print('---')
    print('Predictions:')
    print(predictions)
    print('References:')
    print(transcriptions)
    print('---')

    predictions_all.extend(predictions)
    transcriptions_all.extend(transcriptions)

---
Predictions:
[' І за документом це цея водичезна тна для людни згіпер комбенссціюю, ці лише месенька прибудова до звичайнихї квартири.', ' Тамі миж іншим буд будулиимирелександачи, ми бу були в Лечцінчинні, фовалися з бабуі,, Вона в відітання мі між іншим перед передаває.!!']
References:
['і за документами, ця величезна труна для людини з гіперкомпенсацією – всього лише малесенька прибудова до звичайної квартири.', 'там, між іншим, володимир олександрович, коли ви були у ла́нчині, фотографувалися з бабусею. вона вам вітання, між іншим, передавала. дааа?']
---
---
Predictions:
[' Поренка тестеж,івнюють із гітлером. Б у нас вігітлера протестуюютьть оп опозиція гітлера.', ' Яккц сталося, Все просто, Мь та люди середнього віку переважно проїгну рвала ті вибори']
References:
['порошенка теж порівнюють із гітлером. бо у нас владі гітлера протистоїть – опозиція гітлера.', 'як це сталося? все просто! молодь та люди середнього віку переважно проігнорували ті вибори.']
---
---
Predictions:
[

In [52]:
wer_value = round(wer.compute(predictions=predictions_all, references=transcriptions_all), 4)
cer_value = round(cer.compute(predictions=predictions_all, references=transcriptions_all), 4)

print(f'WER: {wer_value} | CER: {cer_value}')

WER: 0.8148 | CER: 0.2931


## Fine-tuning the model

In [ ]:
from datasets import load_metric
from tqdm.notebook import tqdm

class Trainer:
    def __init__(self, model, processor, train_dataloader: DataLoader, eval_dataloader: DataLoader, test_dataloader: DataLoader,
                 epochs=10, lr=1e-3):
        # logging, parameters, etc
        self.model = model
        self.processor = processor
        self.train_dataloader = train_dataloader
        self.eval_dataloader = eval_dataloader
        self.test_dataloader = test_dataloader
        self.epochs = epochs
        self.lr = lr
        self.criterion = nn.functional.ctc_loss
        self.optimizer = torch.optim.Adam(model.parameters(), lr=lr)
        self.wer_func = load_metric("wer")

    def predict(self, batch):
        # generate prediction of the model (generate sequence) 
        features, labels = batch 
        attention_mask = labels["attention_mask"].to(device)
        labels = labels["input_ids"].to(device)
        input_values = features["input_features"].to(device)
        input_values = input_values.squeeze()

        with torch.no_grad():
            logits = model(input_values, decoder_input_ids=labels).logits

        predicted_ids = torch.argmax(logits, dim=-1)
        predicted_ids = predicted_ids.masked_fill(attention_mask.ne(1), processor.tokenizer.pad_token_id)
        transcription = self.processor.batch_decode(predicted_ids, skip_special_tokens=True)
        
        return transcription

    def train_step(self, batch):
        # calculate loss on single batch
        features, labels = batch 
        attention_mask = labels["attention_mask"].to(device)
        labels = labels["input_ids"].to(device)
        input_values = features["input_features"].to(device)
        input_values = input_values.squeeze()
        
        logits = model(input_values, decoder_input_ids=labels).logits
        log_probs = nn.functional.log_softmax(logits, dim=-1, dtype=torch.float32).transpose(0, 1)
#         print(input_values)

        labels_mask = labels >= 0
        target_lengths = labels_mask.sum(-1)
        flattened_targets = labels.masked_select(labels_mask)

        #  Computes the output length of the convolutional layers
        input_lengths = self.model._get_feat_extract_output_lengths(attention_mask.sum(-1)).to(torch.long)
        
        loss = self.criterion(log_probs, flattened_targets, input_lengths, target_lengths, reduction="mean", blank=36)
#         print(loss)
        
        return loss


    def train_epoch(self, epoch):
        # do backward prob, calculate WER on train epoch
        self.model.train()
        print("Training Epoch ", epoch)
        
        total_loss = 0
        predictions = []
        references = []
        
        for batch in tqdm(self.train_dataloader):
            self.optimizer.zero_grad()
            loss = self.train_step(batch)
            
            loss.backward()
            self.optimizer.step()
            total_loss += loss.item()
            print(loss.item())
            
            _, labels = batch
            labels = labels["input_ids"].to(device)
            prediction = self.predict(batch)
            predictions.extend(prediction)
            transcriptions = self.processor.batch_decode(labels, skip_special_tokens=True)
            references.extend(transcriptions)
            
        total_loss /= len(self.train_dataloader)
        print(f"Epoch {epoch} | Train Loss: {total_loss:.4f}") 
        
        wer = self.wer_func.compute(predictions=predictions, references=references)
        print(f"Training WER: {wer:.4f}")
        
    def train(self):
        for e in range(self.epochs):
            self.train_epoch(e)
            self.validate()

    def validate(self):
        # calculate WER on validation subset
        self.model.eval()
        predictions = []
        references = []
        
        for batch in tqdm(self.eval_dataloader):
            _, labels = batch
            labels = labels["input_ids"].to(device)
            prediction = self.predict(batch)
            predictions.extend(prediction)
            transcriptions = self.processor.batch_decode(labels, skip_special_tokens=True)
            references.extend(transcriptions)
            
        wer = self.wer_func.compute(predictions=predictions, references=references)
        print(f"Validation WER: {wer:.4f}")

    def test(self):
        self.model.eval()
        predictions = []
        references = []
        
        for batch in tqdm(self.test_dataloader):
            _, labels = batch
            labels = labels["input_ids"].to(device)
            prediction = self.predict(batch)
            predictions.extend(prediction)
            transcriptions = self.processor.batch_decode(labels, skip_special_tokens=True)
            references.extend(transcriptions)
            
        wer = self.wer_func.compute(predictions=predictions, references=references)
        print(f"Test WER: {wer:.4f}")

In [56]:
batch_size = 2

train_loader = DataLoader(dataset=WhisperCustomDataset(train_set, processor, sampling_rate),
                            batch_size=batch_size,
                            shuffle=True,
                            collate_fn=collate_fn,
                            )
val_loader = DataLoader(dataset=WhisperCustomDataset(validation_set, processor, sampling_rate),
                            batch_size=batch_size,
                            shuffle=False,
                            collate_fn=collate_fn,
                            )
test_loader = DataLoader(dataset=WhisperCustomDataset(test_set, processor, sampling_rate),
                            batch_size=batch_size,
                            shuffle=False,
                            collate_fn=collate_fn,
                            )

In [ ]:
trainer = Trainer(model, processor, train_loader, val_loader, test_loader, epochs=3, lr=1e-4)
trainer.train()

Training Epoch  0


/opt/conda/lib/python3.10/site-packages/datasets/load.py:756: FutureWarning: The repository for wer contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.18.0/metrics/wer/wer.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric from the next major release of `datasets`.
  warnings.warn(


  0%|          | 0/400 [00:00<?, ?it/s]

inf
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan


In [47]:
trainer.test()

  0%|          | 0/5 [00:00<?, ?it/s]

Test WER: 1.0000


## Conclusion

Even though I didn't manage to find out why I kept getting "nans" in the fine-tuning process, we can still see that the best WER was in the case of Whisper model and "transcribe function" - after doing the same, but using the processor and other following functions, I resulted in WER that was greater than 1 :) However, in the last minute I notice that I forgot to incorporate the attention mask, which decreased the WER to 0.8. 